# Imports and function def

In [1]:
import easyocr
import cv2
from matplotlib import pyplot as plt
import numpy as np

### Function to process the OCR numbers, there are some special cases that are hard coded to recognise certain numbers

In [2]:
def checkNumbers(resL, resR, currL, currR, leftCount, rightCount, leftSameCount, rightSameCount, framecount, momentum):
    if (resL[2] > 0.2):
        ## 1 Because score can only increment, 71 because ocr software sometimes detects 1 as 8 when 10 and above
        if (int(resL[1]) == currL):
            leftSameCount += 1
        elif (int(resL[1]) - currL) == 1 or (int(resL[1]) - currL) == 71 or (int(resL[1]) == 37 and currL == 6):
            leftCount += 1

        if (leftCount == 10):
            currL += 1
            netScore = currL - currR
            momentum.append([framecount + 1, netScore])
            leftCount = 0
        elif (leftSameCount == 10):
            leftCount = 0
                
    if (resR[2] > 0.2):
        if (int(resR[1]) == currR):
            rightSameCount += 1
        elif (int(resR[1]) - currR) == 1 or (int(resR[1]) - currR) == 71 or (int(resR[1]) == 37 and currR == 6):
            rightCount += 1

        if (rightCount == 10):
            currR += 1
            netScore = currL - currR
            momentum.append([framecount + 1, netScore])
            rightCount = 0
        elif (rightSameCount == 10):
            rightCount = 0
        
    return currL, currR, leftCount, rightCount, leftSameCount, rightSameCount, momentum

### Function to check iou of two boxes, may be needed for further optimisation, currently not used

In [17]:
def get_iou(bb1, bb2):
    """
    Calculate the Intersection over Union (IoU) of two bounding boxes.

    Parameters
    ----------
    bb1 : dict
        Keys: {'x1', 'x2', 'y1', 'y2'}
        The (x1, y1) position is at the top left corner,
        the (x2, y2) position is at the bottom right corner
    bb2 : dict
        Keys: {'x1', 'x2', 'y1', 'y2'}
        The (x, y) position is at the top left corner,
        the (x2, y2) position is at the bottom right corner

    Returns
    -------
    float
        in [0, 1]
    """
    assert bb1['x1'] < bb1['x2']
    assert bb1['y1'] < bb1['y2']
    assert bb2['x1'] < bb2['x2']
    assert bb2['y1'] < bb2['y2']

    # determine the coordinates of the intersection rectangle
    x_left = max(bb1['x1'], bb2['x1'])
    y_top = max(bb1['y1'], bb2['y1'])
    x_right = min(bb1['x2'], bb2['x2'])
    y_bottom = min(bb1['y2'], bb2['y2'])

    if x_right < x_left or y_bottom < y_top:
        return 0.0

    # The intersection of two axis-aligned bounding boxes is always an
    # axis-aligned bounding box
    intersection_area = (x_right - x_left) * (y_bottom - y_top)

    # compute the area of both AABBs
    bb1_area = (bb1['x2'] - bb1['x1']) * (bb1['y2'] - bb1['y1'])
    bb2_area = (bb2['x2'] - bb2['x1']) * (bb2['y2'] - bb2['y1'])

    # compute the intersection over union by taking the intersection
    # area and dividing it by the sum of prediction + ground-truth
    # areas - the interesection area
    iou = intersection_area / float(bb1_area + bb2_area - intersection_area)
    assert iou >= 0.0
    assert iou <= 1.0
    return iou

### Wrapper function for the whole OCR processing, but currently gets some weird error

In [14]:
def perform_ocr(vid_url, boxes_df):
    cap = cv2.VideoCapture(vid_url)
    framecount = 0
    reader = easyocr.Reader(['en'])
    momentum = [[1, 0]] # Frame number, score
    netScore = 0 # Left positive, Right negative

    # Variables to keep track of number of frames number has changed
    leftCount = 0
    rightCount = 0

    # These two variables are to check if the number should be the same
    leftSameCount = 0
    rightSameCount = 0

    # Variables to keep track of current score
    currL = 0
    currR = 0

    # Variables to ensure that we can capture the scoreboard
    cantFindCount = 0
    found = False
    posList = []
    def onMousePisteCorners(event, x, y, flags, param):
       global posList
       if event == cv2.EVENT_LBUTTONDOWN:
            np.append(posList, [x,y])

    pts2 = np.array([[0,0], [0,360], [540,0], [540,360]], np.float32)

    while(True):
        ret, frame = cap.read()

        if ret == True:

            if not found:
                boxlist = boxes_df.iloc[framecount]
            frame = frame[int(boxlist[1])-20:int(boxlist[3])+20, int(boxlist[0])-20:int(boxlist[2])+20]

            res = cv2.resize(frame,None,fx=8, fy=8, interpolation = cv2.INTER_CUBIC)
            if not found:
                cv2.imshow('WindowName', res)
                cv2.setMouseCallback('WindowName', onMousePisteCorners)

                while(1):
                    if cv2.waitKey(10) & 0xFF==ord('q'):
                        cv2.destroyAllWindows()
                        break
                posList = np.float32(posList)
                found = True

            gray = cv2.cvtColor(res, cv2.COLOR_BGR2GRAY)

            ret, newimage = cv2.threshold(gray,100,255,cv2.THRESH_BINARY_INV)
            frame = newimage

            matrix = cv2.getPerspectiveTransform(posList, pts2)
            frame = cv2.warpPerspective(frame, matrix, (540,360))
            h = frame.shape[0]
            w = frame.shape[1]

            resL = reader.recognize(frame, [[0, int(w*0.37), int(h*0.57), h]], [], allowlist='0123456789')[0]
            resR = reader.recognize(frame, [[int(w*0.65), w, int(h*0.57), h]], [], allowlist='0123456789')[0]

            frame = cv2.rectangle(frame, (0, int(h*0.57)), (int(w*0.37), h), (0,0,0), 3)
            frame = cv2.rectangle(frame, (int(w*0.65), int(h*0.57)), (w, h), (0,0,0), 3)

            currL, currR, leftCount, rightCount, leftSameCount, rightSameCount, momentum = checkNumbers(resL, resR, currL, currR, leftCount, rightCount, leftSameCount, rightSameCount, framecount, momentum)

            if (resL[2] > 0.2 and resR[2] > 0.2):
                output = (resL[1], resR[1])
                print(output)

            if (resL[2] < 0.1 or resR[2] < 0.1):
                cantFindCount += 1
                if cantFindCount == 30:
                    found = False
                    posList = []
            else:
                cantFindCount = 0


            cv2.imshow('frame',frame)
            framecount += 1
            if cv2.waitKey(1) & 0xFF == ord('r'):
                found = False
                posList = []
            if cv2.waitKey(1) & 0xFF == ord('q'):
                break
        else:
            break
    cv2.destroyAllWindows() 
    cap.release()
    return momentum

## Using easyocr on RobVsHkg

In [3]:
import pandas as pd

boxes_df = pd.read_csv('RobVsHkg/boxes.csv', header=None)
boxes_df.head()

0    1     2    3
0  938  301  1003  343
1  938  301  1003  343
2  938  301  1003  343
3  938  301  1003  343
4  938  301  1003  343

### Below is the weird error that occurs when trying to use the wrapper function

In [15]:
momentum = perform_ocr("RobVsHkg/masked.mp4", boxes_df)

error: OpenCV(4.8.1) D:\a\opencv-python\opencv-python\opencv\modules\imgproc\src\imgwarp.cpp:3528: error: (-215:Assertion failed) src.checkVector(2, CV_32F) == 4 && dst.checkVector(2, CV_32F) == 4 in function 'cv::getPerspectiveTransform'


### Actual OCR

In [16]:
cap = cv2.VideoCapture("RobVsHkg/masked.mp4")
framecount = 0
reader = easyocr.Reader(['en'])
momentum = [[1, 0]] # Frame number, score
netScore = 0 # Left positive, Right negative

# Variables to keep track of number of frames number has changed
leftCount = 0
rightCount = 0

# These two variables are to check if the number should be the same
leftSameCount = 0
rightSameCount = 0

# Variables to keep track of current score
currL = 0
currR = 0

# Variables to ensure that we can capture the scoreboard
cantFindCount = 0
found = False
posList = []
def onMousePisteCorners(event, x, y, flags, param):
   global posList
   if event == cv2.EVENT_LBUTTONDOWN:
        posList.append([x, y])

pts2 = [[0,0], [0,360], [540,0], [540,360]]

while(True):
    ret, frame = cap.read()
    
    if ret == True:

        if not found:
            boxlist = boxes_df.iloc[framecount]
        frame = frame[int(boxlist[1])-20:int(boxlist[3])+20, int(boxlist[0])-20:int(boxlist[2])+20]
        
        res = cv2.resize(frame,None,fx=8, fy=8, interpolation = cv2.INTER_CUBIC)
        if not found:
            cv2.imshow('WindowName', res)
            cv2.setMouseCallback('WindowName', onMousePisteCorners)

            while(1):
                if cv2.waitKey(10) & 0xFF==ord('q'):
                    cv2.destroyAllWindows()
                    break
            posList = np.float32(posList)
            pts2 = np.float32(pts2)
            found = True

        gray = cv2.cvtColor(res, cv2.COLOR_BGR2GRAY)
        
        ret, newimage = cv2.threshold(gray,100,255,cv2.THRESH_BINARY_INV)
        frame = newimage
        
        matrix = cv2.getPerspectiveTransform(posList, pts2)
        frame = cv2.warpPerspective(frame, matrix, (540,360))
        h = frame.shape[0]
        w = frame.shape[1]
        
        resL = reader.recognize(frame, [[0, int(w*0.37), int(h*0.57), h]], [], allowlist='0123456789')[0]
        resR = reader.recognize(frame, [[int(w*0.65), w, int(h*0.57), h]], [], allowlist='0123456789')[0]

        frame = cv2.rectangle(frame, (0, int(h*0.57)), (int(w*0.37), h), (0,0,0), 3)
        frame = cv2.rectangle(frame, (int(w*0.65), int(h*0.57)), (w, h), (0,0,0), 3)
        
        currL, currR, leftCount, rightCount, leftSameCount, rightSameCount, momentum = checkNumbers(resL, resR, currL, currR, leftCount, rightCount, leftSameCount, rightSameCount, framecount, momentum)
        
        if (resL[2] > 0.2 and resR[2] > 0.2):
            output = (resL[1], resR[1])
            print(output)
            
        if (resL[2] < 0.1 or resR[2] < 0.1):
            cantFindCount += 1
            if cantFindCount == 30:
                found = False
                posList = []
        else:
            cantFindCount = 0
                
        
        cv2.imshow('frame',frame)
        framecount += 1
        if cv2.waitKey(1) & 0xFF == ord('r'):
            found = False
            posList = []
        if cv2.waitKey(1) & 0xFF == ord('q'):
            break
    else:
        break
cv2.destroyAllWindows() 
cap.release()

('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')

('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')

('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')

('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')

('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')
('2', '0')

...

('13', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('123', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('123', '2')
('123', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('123', '2')
('123', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')

('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12', '2')
('12

('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('3', '2')
('3', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13',

('13', '2')
('13', '2')
('13', '2')
('13', '2')
('3', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13', '2')
('13'

('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('85', '2')
('15', '2')
('85', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15', '2')
('15

### Checking and saving results

In [18]:
res = []
print(len(momentum))
for m in momentum:
    res.append([m[0] / 30, m[1]])
result = list(zip(*res))
result

18


[(0.03333333333333333,
  10.433333333333334,
  47.86666666666667,
  112.03333333333333,
  119.7,
  129.53333333333333,
  147.86666666666667,
  167.13333333333333,
  179.26666666666668,
  208.76666666666668,
  235.33333333333334,
  259.8666666666667,
  289.3333333333333,
  311.8666666666667,
  417.4,
  449.1333333333333,
  491.6333333333333,
  508.0),
 (0, 1, 2, 1, 2, 3, 4, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13)]

In [19]:
results_df = pd.DataFrame(res)
results_df
results_df.to_csv('RobVsHkg/momentum_results.csv', index=False, header=False)

## Note the rest of the processing is actually just a copy of the above, since the wrapper method does not work I had to copy paste...

## EasyOCR on hkgvsmax

In [90]:
import pandas as pd

boxes_df = pd.read_csv('hkgvsmax/boxes.csv', header=None)
boxes_df.head()

0    1     2    3
0  935  363  1000  415
1  935  363  1000  415
2  935  363  1000  415
3  935  363  1000  415
4  935  363  1000  415

In [91]:
cap = cv2.VideoCapture("hkgvsmax/masked.mp4")
framecount = 0
reader = easyocr.Reader(['en'])
momentum = [[1, 0]] # Frame number, score
netScore = 0 # Left positive, Right negative

# Variables to keep track of number of frames number has changed
leftCount = 0
rightCount = 0

# These two variables are to check if the number should be the same
leftSameCount = 0
rightSameCount = 0

# Variables to keep track of current score
currL = 0
currR = 0

# Variables to ensure that we can capture the scoreboard
cantFindCount = 0
found = False
posList = []
def onMousePisteCorners(event, x, y, flags, param):
   global posList
   if event == cv2.EVENT_LBUTTONDOWN:
        posList.append([x, y])

pts2 = [[0,0], [0,360], [540,0], [540,360]]

while(True):
    ret, frame = cap.read()
    
    if ret == True:

        if not found:
            boxlist = boxes_df.iloc[framecount]
        frame = frame[int(boxlist[1])-20:int(boxlist[3])+20, int(boxlist[0])-20:int(boxlist[2])+20]
        
        res = cv2.resize(frame,None,fx=8, fy=8, interpolation = cv2.INTER_CUBIC)
        if not found:
            cv2.imshow('WindowName', res)
            cv2.setMouseCallback('WindowName', onMousePisteCorners)

            while(1):
                if cv2.waitKey(10) & 0xFF==ord('q'):
                    cv2.destroyAllWindows()
                    break
            posList = np.float32(posList)
            pts2 = np.float32(pts2)
            found = True

        gray = cv2.cvtColor(res, cv2.COLOR_BGR2GRAY)
        
        ret, newimage = cv2.threshold(gray,100,255,cv2.THRESH_BINARY_INV)
        frame = newimage
        
        matrix = cv2.getPerspectiveTransform(posList, pts2)
        frame = cv2.warpPerspective(frame, matrix, (540,360))
        h = frame.shape[0]
        w = frame.shape[1]
        
        resL = reader.recognize(frame, [[0, int(w*0.37), int(h*0.57), h]], [], allowlist='0123456789')[0]
        resR = reader.recognize(frame, [[int(w*0.65), w, int(h*0.57), h]], [], allowlist='0123456789')[0]

        frame = cv2.rectangle(frame, (0, int(h*0.57)), (int(w*0.37), h), (0,0,0), 3)
        frame = cv2.rectangle(frame, (int(w*0.65), int(h*0.57)), (w, h), (0,0,0), 3)
        
        currL, currR, leftCount, rightCount, leftSameCount, rightSameCount, momentum = checkNumbers(resL, resR, currL, currR, leftCount, rightCount, leftSameCount, rightSameCount, framecount, momentum)
        
        if (resL[2] > 0.2 and resR[2] > 0.2):
            output = (resL[1], resR[1])
            print(output)
            
        if (resL[2] < 0.1 or resR[2] < 0.1):
            cantFindCount += 1
            if cantFindCount == 30:
                found = False
                posList = []
        else:
            cantFindCount = 0
                
        
        cv2.imshow('frame',frame)
        framecount += 1
        if cv2.waitKey(1) & 0xFF == ord('r'):
            found = False
            posList = []
        if cv2.waitKey(1) & 0xFF == ord('q'):
            break
    else:
        break
cv2.destroyAllWindows() 
cap.release()

('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')

('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('27', '0')
('7', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0'

('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')

('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')

('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '05')
('5', '0')
('5', '05')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0

...

('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('3', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('3', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('3', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', 

('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '6')
('13', '47')
('13', '47')
('13', '47')
('13', '7')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '37')
('13', '47')
('13', '37')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '7')
('13', '47')
('13', '37')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '7')
('13', '7')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13', '47')
('13',

('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14

('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('04', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('04', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14', '8')
('14

('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')
('15', '8')


In [92]:
res = []
print(len(momentum))
for m in momentum:
    res.append([m[0] / 30, m[1]])
result = list(zip(*res))
result

24


[(0.03333333333333333,
  16.266666666666666,
  29.033333333333335,
  43.86666666666667,
  85.06666666666666,
  96.96666666666667,
  116.13333333333334,
  156.13333333333333,
  205.8,
  218.26666666666668,
  224.33333333333334,
  280.5,
  294.9,
  308.6,
  332.56666666666666,
  374.06666666666666,
  400.8333333333333,
  419.53333333333336,
  431.5,
  462.73333333333335,
  572.5,
  583.7666666666667,
  600.2333333333333,
  648.4666666666667),
 (0, 1, 2, 3, 4, 5, 4, 5, 6, 7, 8, 9, 8, 9, 8, 9, 10, 9, 8, 7, 6, 7, 6, 7)]

In [93]:
results_df = pd.DataFrame(res)
results_df
results_df.to_csv('hkgvsmax/momentum_results.csv', index=False, header=False)

## Easyocr wzvskor

In [86]:
import pandas as pd

boxes_df = pd.read_csv('wzvskor/boxes.csv', header=None)
boxes_df.head()

0    1    2    3
0  922  293  998  359
1  922  293  998  359
2  922  293  998  359
3  922  293  998  359
4  922  293  998  359

In [87]:
cap = cv2.VideoCapture("wzvskor/masked.mp4")
framecount = 0
reader = easyocr.Reader(['en'])
momentum = [[1, 0]] # Frame number, score
netScore = 0 # Left positive, Right negative

# Variables to keep track of number of frames number has changed
leftCount = 0
rightCount = 0

# These two variables are to check if the number should be the same
leftSameCount = 0
rightSameCount = 0

# Variables to keep track of current score
currL = 0
currR = 0

# Variables to ensure that we can capture the scoreboard
cantFindCount = 0
found = False
posList = []
def onMousePisteCorners(event, x, y, flags, param):
   global posList
   if event == cv2.EVENT_LBUTTONDOWN:
        posList.append([x, y])

pts2 = [[0,0], [0,360], [540,0], [540,360]]

while(True):
    ret, frame = cap.read()
    
    if ret == True:

        if not found:
            boxlist = boxes_df.iloc[framecount]
        frame = frame[int(boxlist[1])-20:int(boxlist[3])+20, int(boxlist[0])-20:int(boxlist[2])+20]
        
        res = cv2.resize(frame,None,fx=8, fy=8, interpolation = cv2.INTER_CUBIC)
        if not found:
            cv2.imshow('WindowName', res)
            cv2.setMouseCallback('WindowName', onMousePisteCorners)

            while(1):
                if cv2.waitKey(10) & 0xFF==ord('q'):
                    cv2.destroyAllWindows()
                    break
            posList = np.float32(posList)
            pts2 = np.float32(pts2)
            found = True

        gray = cv2.cvtColor(res, cv2.COLOR_BGR2GRAY)
        
        ret, newimage = cv2.threshold(gray,100,255,cv2.THRESH_BINARY_INV)
        frame = newimage
        
        matrix = cv2.getPerspectiveTransform(posList, pts2)
        frame = cv2.warpPerspective(frame, matrix, (540,360))
        h = frame.shape[0]
        w = frame.shape[1]
        
        resL = reader.recognize(frame, [[0, int(w*0.37), int(h*0.57), h]], [], allowlist='0123456789')[0]
        resR = reader.recognize(frame, [[int(w*0.65), w, int(h*0.57), h]], [], allowlist='0123456789')[0]

        frame = cv2.rectangle(frame, (0, int(h*0.57)), (int(w*0.37), h), (0,0,0), 3)
        frame = cv2.rectangle(frame, (int(w*0.65), int(h*0.57)), (w, h), (0,0,0), 3)
        
        currL, currR, leftCount, rightCount, leftSameCount, rightSameCount, momentum = checkNumbers(resL, resR, currL, currR, leftCount, rightCount, leftSameCount, rightSameCount, framecount, momentum)
        
        if (resL[2] > 0.2 and resR[2] > 0.2):
            output = (resL[1], resR[1])
            print(output)
            
        if (resL[2] < 0.1 or resR[2] < 0.1):
            cantFindCount += 1
            if cantFindCount == 30:
                found = False
                posList = []
        else:
            cantFindCount = 0
                
        
        cv2.imshow('frame',frame)
        framecount += 1
        if cv2.waitKey(1) & 0xFF == ord('r'):
            found = False
            posList = []
        if cv2.waitKey(1) & 0xFF == ord('q'):
            break
    else:
        break
cv2.destroyAllWindows() 
cap.release()

('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')

('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')

('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')

('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '4')
('0', '4')
('0', '4')
('0', '4')
('0', '4')
('0', '4')
('0', '4')
('0', '4')

('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')
('1', '5')

...

('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')
('3', '8')

('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '9')
('3', '19')
('3', '10')
('3', '10')
('3', '10')
('3', '10')
('3', '10')
('3', '10')
('3', '10')
('3', '10')
('3', '10')
('3', '10')
('3', '10'

('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4', '10')
('4'

('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4', '12')
('4'

('4', '13')
('4', '13')
('4', '13')
('4', '13')
('4', '13')
('4', '13')
('4', '13')
('4', '13')
('4', '13')
('4', '13')
('4', '13')
('4', '13')
('4', '13')
('4', '13')
('4', '13')
('4', '13')
('4', '13')
('4', '13')
('4', '13')
('4', '13')
('4', '13')
('4', '13')
('4', '13')
('4', '13')
('4', '13')
('4', '13')
('4', '13')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4', '14')
('4'

In [88]:
res = []
print(len(momentum))
for m in momentum:
    res.append([m[0] / 30, m[1]])
result = list(zip(*res))
result

20


[(0.03333333333333333,
  37.63333333333333,
  50.0,
  67.8,
  77.7,
  84.9,
  101.33333333333333,
  135.56666666666666,
  143.73333333333332,
  158.0,
  169.76666666666668,
  185.66666666666666,
  267.3,
  276.8333333333333,
  293.1,
  303.8333333333333,
  316.53333333333336,
  327.6333333333333,
  343.73333333333335,
  360.6666666666667),
 (0,
  -1,
  -2,
  -3,
  -4,
  -5,
  -4,
  -5,
  -4,
  -5,
  -4,
  -5,
  -6,
  -7,
  -6,
  -7,
  -8,
  -9,
  -10,
  -11)]

In [89]:
results_df = pd.DataFrame(res)
results_df
results_df.to_csv('wzvskor/momentum_results.csv', index=False, header=False)

## Easyocr samvskor

In [75]:
import pandas as pd

boxes_df = pd.read_csv('samvskor/boxes.csv', header=None)
boxes_df.head()

0    1    2    3
0  915  343  977  392
1  914  344  977  392
2  914  343  976  392
3  914  343  976  392
4  914  343  977  392

In [83]:
cap = cv2.VideoCapture("samvskor/masked.mp4")
framecount = 0
reader = easyocr.Reader(['en'])
momentum = [[1, 0]] # Frame number, score
netScore = 0 # Left positive, Right negative

# Variables to keep track of number of frames number has changed
leftCount = 0
rightCount = 0

# These two variables are to check if the number should be the same
leftSameCount = 0
rightSameCount = 0

# Variables to keep track of current score
currL = 0
currR = 0

# Variables to ensure that we can capture the scoreboard
cantFindCount = 0
found = False
posList = []
def onMousePisteCorners(event, x, y, flags, param):
   global posList
   if event == cv2.EVENT_LBUTTONDOWN:
        posList.append([x, y])

pts2 = [[0,0], [0,360], [540,0], [540,360]]

while(True):
    ret, frame = cap.read()
    
    if ret == True:

        if not found:
            boxlist = boxes_df.iloc[framecount]
        frame = frame[int(boxlist[1])-20:int(boxlist[3])+20, int(boxlist[0])-20:int(boxlist[2])+20]
        
        res = cv2.resize(frame,None,fx=8, fy=8, interpolation = cv2.INTER_CUBIC)
        if not found:
            cv2.imshow('WindowName', res)
            cv2.setMouseCallback('WindowName', onMousePisteCorners)

            while(1):
                if cv2.waitKey(10) & 0xFF==ord('q'):
                    cv2.destroyAllWindows()
                    break
            posList = np.float32(posList)
            pts2 = np.float32(pts2)
            found = True

        gray = cv2.cvtColor(res, cv2.COLOR_BGR2GRAY)
        
        ret, newimage = cv2.threshold(gray,100,255,cv2.THRESH_BINARY_INV)
        frame = newimage
        
        matrix = cv2.getPerspectiveTransform(posList, pts2)
        frame = cv2.warpPerspective(frame, matrix, (540,360))
        h = frame.shape[0]
        w = frame.shape[1]
        
        resL = reader.recognize(frame, [[0, int(w*0.37), int(h*0.57), h]], [], allowlist='0123456789')[0]
        resR = reader.recognize(frame, [[int(w*0.65), w, int(h*0.57), h]], [], allowlist='0123456789')[0]

        frame = cv2.rectangle(frame, (0, int(h*0.57)), (int(w*0.37), h), (0,0,0), 3)
        frame = cv2.rectangle(frame, (int(w*0.65), int(h*0.57)), (w, h), (0,0,0), 3)
        
        currL, currR, leftCount, rightCount, leftSameCount, rightSameCount, momentum = checkNumbers(resL, resR, currL, currR, leftCount, rightCount, leftSameCount, rightSameCount, framecount, momentum)
        
        if (resL[2] > 0.2 and resR[2] > 0.2):
            output = (resL[1], resR[1])
            print(output)
            
        if (resL[2] < 0.1 or resR[2] < 0.1):
            cantFindCount += 1
            if cantFindCount == 30:
                found = False
                posList = []
        else:
            cantFindCount = 0
                
        
        cv2.imshow('frame',frame)
        framecount += 1
        if cv2.waitKey(1) & 0xFF == ord('r'):
            found = False
            posList = []
        if cv2.waitKey(1) & 0xFF == ord('q'):
            break
    else:
        break
cv2.destroyAllWindows() 
cap.release()

('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')

('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')

('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')

('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')

('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')

...

('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('0', '14')
('10', '14')
('10', '14')
('10', '14')
('10', '14')
('10', '14')
('10', '14')
('10', '14')
('10', '14')
('10', '14')
('10', '14')
('10', '14')
('10', '14')
('10', '14')
('10', '14')
('10', '14')
('10', '14')
('10', '14')
('10', '14')
('10', '14

('17', '14')
('17', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('17', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('17', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('11', '14')
('11', '14')

('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('1', '14')
('1', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('11', '14')
('11', '14')
('11', '14')
('1', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('11', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('1', '14')
('1', '14')
('1', '14')
('1', '14')
('1', '14')
('1', '

('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('7', '14')
('17', '14')
('7', '14')
('17', '14')
('7', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('17', '14')
('7', '14')
('7', '14')
('7', '14')
('17', '14')
('17', '14')
('17', '14')
('1', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('12', '14')
('12', '14')
('12', '14')
('12', '14')
('12', '14')
('12', '14')
('12', '14')
('12', '14')
('12', '14')
('12', '14')
('12', '14')
('12', '14')
('12', '14')
('12', '14')
('12', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('12', '14')
('12', '14')
('12', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('12', '14')
('12', '14')
('12', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2',

('12', '14')
('12', '14')
('12', '14')
('12', '14')
('12', '14')
('2', '14')
('12', '14')
('2', '14')
('2', '14')
('12', '14')
('12', '14')
('12', '14')
('12', '14')
('12', '14')
('12', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('12', '14')
('12', '14')
('12', '14')
('12', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('12', '14')
('12', '14')
('12', '14')
('12', '14')
('12', '14')
('12', '14')
('12', '14')
('2', '14')
('12', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('12', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('12', '14')
('12', '14')
('12', '14')
('12', '14')
('12', '14')
('12', '14')
('12', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '14')
('2', '1

In [84]:
res = []
print(len(momentum))
for m in momentum:
    res.append([m[0] / 30, m[1]])
result = list(zip(*res))
result

28


[(0.03333333333333333,
  136.56666666666666,
  160.1,
  172.73333333333332,
  207.76666666666668,
  233.03333333333333,
  337.46666666666664,
  337.6,
  353.5,
  354.8666666666667,
  413.3,
  444.1,
  501.03333333333336,
  505.1666666666667,
  531.2333333333333,
  547.0,
  665.5,
  692.2333333333333,
  731.2,
  737.0,
  745.4333333333333,
  770.6333333333333,
  773.0333333333333,
  802.2666666666667,
  804.2,
  819.0333333333333,
  885.2333333333333,
  910.9333333333333),
 (0,
  1,
  0,
  1,
  0,
  -1,
  0,
  -1,
  -2,
  -1,
  0,
  -1,
  -2,
  -1,
  -2,
  -3,
  -4,
  -3,
  -2,
  -3,
  -4,
  -5,
  -4,
  -5,
  -4,
  -3,
  -2,
  -3)]

In [85]:
results_df = pd.DataFrame(res)
results_df
results_df.to_csv('samvskor/momentum_results.csv', index=False, header=False)

## Easyocr kazvselliot


In [71]:
import pandas as pd

boxes_df = pd.read_csv('kazvselliot/boxes.csv', header=None)
boxes_df.head()

0    1    2    3
0  925  344  990  394
1  925  345  990  394
2  925  345  990  394
3  925  344  991  394
4  925  345  990  394

In [72]:
cap = cv2.VideoCapture("kazvselliot/masked.mp4")
framecount = 0
reader = easyocr.Reader(['en'])
momentum = [[1, 0]] # Frame number, score
netScore = 0 # Left positive, Right negative

# Variables to keep track of number of frames number has changed
leftCount = 0
rightCount = 0

# These two variables are to check if the number should be the same
leftSameCount = 0
rightSameCount = 0

# Variables to keep track of current score
currL = 0
currR = 0

# Variables to ensure that we can capture the scoreboard
cantFindCount = 0
found = False
posList = []
def onMousePisteCorners(event, x, y, flags, param):
   global posList
   if event == cv2.EVENT_LBUTTONDOWN:
        posList.append([x, y])

pts2 = [[0,0], [0,360], [540,0], [540,360]]

while(True):
    ret, frame = cap.read()
    
    if ret == True:

        if not found:
            boxlist = boxes_df.iloc[framecount]
        frame = frame[int(boxlist[1])-20:int(boxlist[3])+20, int(boxlist[0])-20:int(boxlist[2])+20]
        
        res = cv2.resize(frame,None,fx=8, fy=8, interpolation = cv2.INTER_CUBIC)
        if not found:
            cv2.imshow('WindowName', res)
            cv2.setMouseCallback('WindowName', onMousePisteCorners)

            while(1):
                if cv2.waitKey(10) & 0xFF==ord('q'):
                    cv2.destroyAllWindows()
                    break
            posList = np.float32(posList)
            pts2 = np.float32(pts2)
            found = True

        gray = cv2.cvtColor(res, cv2.COLOR_BGR2GRAY)
        
        ret, newimage = cv2.threshold(gray,100,255,cv2.THRESH_BINARY_INV)
        frame = newimage
        
        matrix = cv2.getPerspectiveTransform(posList, pts2)
        frame = cv2.warpPerspective(frame, matrix, (540,360))
        h = frame.shape[0]
        w = frame.shape[1]
        
        resL = reader.recognize(frame, [[0, int(w*0.37), int(h*0.57), h]], [], allowlist='0123456789')[0]
        resR = reader.recognize(frame, [[int(w*0.65), w, int(h*0.57), h]], [], allowlist='0123456789')[0]

        frame = cv2.rectangle(frame, (0, int(h*0.57)), (int(w*0.37), h), (0,0,0), 3)
        frame = cv2.rectangle(frame, (int(w*0.65), int(h*0.57)), (w, h), (0,0,0), 3)
        
        currL, currR, leftCount, rightCount, leftSameCount, rightSameCount, momentum = checkNumbers(resL, resR, currL, currR, leftCount, rightCount, leftSameCount, rightSameCount, framecount, momentum)
        
        if (resL[2] > 0.2 and resR[2] > 0.2):
            output = (resL[1], resR[1])
            print(output)
            
        if (resL[2] < 0.1 or resR[2] < 0.1):
            cantFindCount += 1
            if cantFindCount == 30:
                found = False
                posList = []
        else:
            cantFindCount = 0
                
        
        cv2.imshow('frame',frame)
        framecount += 1
        if cv2.waitKey(1) & 0xFF == ord('r'):
            found = False
            posList = []
        if cv2.waitKey(1) & 0xFF == ord('q'):
            break
    else:
        break
cv2.destroyAllWindows() 
cap.release()

('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')

('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('7', '0')
('7', '0')
('7', '0')
('6', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '7')
('0', '37')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0'

('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('3', '0')
('3', '0')
('3', '0')
('3', '0')
('5', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('04', '0')
('04', '0')
('0', '10')
('0', '70')
('0', '10')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('04', '0')
('02', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('03', '0')
('04', '0')
('03', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '40')
('0', '40')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0'

('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '3')
('0', '38')
('0', '7')
('0', '10')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0

('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('3', '1')
('2', '1')
('2', '1')
('2', '1')

...

('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')
('9', '5')

('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('40', '5')
('0', '5')
('10', '5')
('40', '5')
('40', '5')
('40', '5')
('40', '5')
('40', '5')
('40', '5')
('40', '5')
('40', '5')
('40', '5')
('40', '5')
('40', '5')
('40', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('40', '5')
('40', '5')
('0', '5')
('40', '5')
('40', '5')
('40', '5')
('40', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('40', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('40', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')
('0', '5')

('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('0', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01', '5')
('01'

('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '37')
('13', '7')
('13', '7')
('13', '7')
('13', '7')
('13', '7')
('13', '7')
('13', '7')
('13',

('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('04', '37')
('04', '37')
('14', '37')
('04', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')
('04', '37')

In [73]:
res = []
print(len(momentum))
for m in momentum:
    res.append([m[0] / 30, m[1]])
result = list(zip(*res))
result

17


[(0.03333333333333333,
  100.93333333333334,
  111.9,
  114.66666666666667,
  131.13333333333333,
  223.76666666666668,
  254.5,
  273.93333333333334,
  364.1333333333333,
  385.23333333333335,
  406.1333333333333,
  426.2,
  461.8,
  479.03333333333336,
  480.1,
  549.0,
  557.9333333333333),
 (0, 1, 0, 1, 2, 1, 2, 1, 0, 1, 2, 3, 4, 5, 4, 3, 2)]

In [74]:
results_df = pd.DataFrame(res)
results_df
results_df.to_csv('kazvselliot/momentum_results.csv', index=False, header=False)

## Max vs tpe

In [67]:
import pandas as pd

boxes_df = pd.read_csv('maxvstpe/boxes.csv', header=None)
boxes_df.head()

0    1    2    3
0  921  336  998  404
1  924  335  997  403
2  924  335  997  403
3  921  335  998  403
4  922  335  998  403

In [68]:
cap = cv2.VideoCapture("maxvstpe/masked.mp4")
framecount = 0
reader = easyocr.Reader(['en'])
momentum = [[1, 0]] # Frame number, score
netScore = 0 # Left positive, Right negative

# Variables to keep track of number of frames number has changed
leftCount = 0
rightCount = 0

# These two variables are to check if the number should be the same
leftSameCount = 0
rightSameCount = 0

# Variables to keep track of current score
currL = 0
currR = 0

# Variables to ensure that we can capture the scoreboard
cantFindCount = 0
found = False
posList = []
def onMousePisteCorners(event, x, y, flags, param):
   global posList
   if event == cv2.EVENT_LBUTTONDOWN:
        posList.append([x, y])

pts2 = [[0,0], [0,360], [540,0], [540,360]]

while(True):
    ret, frame = cap.read()
    
    if ret == True:

        if not found:
            boxlist = boxes_df.iloc[framecount]
        frame = frame[int(boxlist[1])-20:int(boxlist[3])+20, int(boxlist[0])-20:int(boxlist[2])+20]
        
        res = cv2.resize(frame,None,fx=8, fy=8, interpolation = cv2.INTER_CUBIC)
        if not found:
            cv2.imshow('WindowName', res)
            cv2.setMouseCallback('WindowName', onMousePisteCorners)

            while(1):
                if cv2.waitKey(10) & 0xFF==ord('q'):
                    cv2.destroyAllWindows()
                    break
            posList = np.float32(posList)
            pts2 = np.float32(pts2)
            found = True

        gray = cv2.cvtColor(res, cv2.COLOR_BGR2GRAY)
        
        ret, newimage = cv2.threshold(gray,100,255,cv2.THRESH_BINARY_INV)
        frame = newimage
        
        matrix = cv2.getPerspectiveTransform(posList, pts2)
        frame = cv2.warpPerspective(frame, matrix, (540,360))
        h = frame.shape[0]
        w = frame.shape[1]
        
        resL = reader.recognize(frame, [[0, int(w*0.37), int(h*0.57), h]], [], allowlist='0123456789')[0]
        resR = reader.recognize(frame, [[int(w*0.65), w, int(h*0.57), h]], [], allowlist='0123456789')[0]

        frame = cv2.rectangle(frame, (0, int(h*0.57)), (int(w*0.37), h), (0,0,0), 3)
        frame = cv2.rectangle(frame, (int(w*0.65), int(h*0.57)), (w, h), (0,0,0), 3)
        
        currL, currR, leftCount, rightCount, leftSameCount, rightSameCount, momentum = checkNumbers(resL, resR, currL, currR, leftCount, rightCount, leftSameCount, rightSameCount, framecount, momentum)
        
        if (resL[2] > 0.2 and resR[2] > 0.2):
            output = (resL[1], resR[1])
            print(output)
            
        if (resL[2] < 0.1 or resR[2] < 0.1):
            cantFindCount += 1
            if cantFindCount == 30:
                found = False
                posList = []
        else:
            cantFindCount = 0
                
        
        cv2.imshow('frame',frame)
        framecount += 1
        if cv2.waitKey(1) & 0xFF == ord('r'):
            found = False
            posList = []
        if cv2.waitKey(1) & 0xFF == ord('q'):
            break
    else:
        break
cv2.destroyAllWindows() 
cap.release()

('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '3')
('0', '8')
('8', '8')
('8', '0')
('8', '0')
('8', '8')
('8', '8')
('0', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('0', '8')
('8', '8')
('8', '8')
('8', '0')
('8', '8')
('8', '0')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('0', '8')
('8', '8')
('8', '0')
('8', '8')
('0', '8')
('8', '8')
('0', '8')
('8', '8')
('8', '8')
('0', '8')
('0', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('0', '0')
('8', '8')
('8', '8')
('8', '8')
('8', '0')
('8', '8')
('0', '8')
('8', '0')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '0')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('0', '0')
('8', '8')
('8', '0')
('8', '8')
('8', '0')
('8', '8')
('8', '8')
('8', '8')

('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')

('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')
('2', '8')

('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')

('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('2', '3')
('3', '3')
('3', '3')
('3', '3')
('3', '3')
('3', '3')
('3', '3')
('3', '3')

...

('83', '80')
('83', '80')
('83', '80')
('83', '80')
('83', '80')
('83', '80')
('13', '80')
('13', '80')
('13', '80')
('83', '80')
('83', '80')
('83', '80')
('83', '80')
('83', '80')
('83', '80')
('83', '80')
('13', '80')
('13', '80')
('13', '80')
('13', '80')
('13', '80')
('13', '80')
('13', '80')
('13', '80')
('13', '80')
('13', '80')
('13', '80')
('13', '80')
('13', '80')
('13', '80')
('13', '80')
('13', '80')
('13', '80')
('13', '80')
('83', '80')
('13', '80')
('13', '80')
('13', '80')
('13', '80')
('13', '80')
('13', '80')
('13', '80')
('83', '10')
('83', '10')
('83', '10')
('13', '10')
('13', '10')
('13', '10')
('13', '10')
('83', '10')
('13', '10')
('13', '10')
('13', '10')
('13', '10')
('13', '10')
('13', '10')
('13', '10')
('13', '10')
('13', '10')
('13', '10')
('13', '10')
('13', '10')
('13', '10')
('13', '10')
('13', '10')
('13', '10')
('13', '10')
('13', '10')
('13', '10')
('13', '10')
('13', '10')
('13', '10')
('13', '10')
('13', '10')
('83', '10')
('83', '10')
('83', '10')

('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('14', '80')
('44', '80')
('44', '80')
('14', '80')
('14', '80')
('14', '80')
('14', '80')
('14', '80')
('44', '80')
('44', '80')
('44', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '10')
('84', '80')
('84', '10')
('84', '10')
('84', '10')
('84', '10')
('84', '10')
('84', '10')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '10')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')
('84', '80')

('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('34', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')

('84', '11')
('84', '1')
('84', '11')
('84', '11')
('84', '1')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('44', '11')
('44', '11')
('44', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('44', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
(

('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('14', '11')
('44', '11')
('14', '11')
('14', '11')
('14', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('44', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('84', '11')
('44', '11')
('44', '11')
('44', '11')
('44', '81')
('44', '81')
('44', '81')
('4', '11')
('4', '81')
('44', '81')
('44', '81')
('4', '81')
('44', '81')
('84', '11')
('84', '81')
('84', '11')
('84', '81')
('84', '81')
('14', '81')
('14', '81')
('14', '81')
('14', '81')
('14', '81')
('14', '81')
('14', '81')
('14', '81')
('14', '81')
('14', '81')
('14', '81')
('

In [69]:
res = []
print(len(momentum))
for m in momentum:
    res.append([m[0] / 30, m[1]])
result = list(zip(*res))
result

21


[(0.03333333333333333,
  27.833333333333332,
  44.96666666666667,
  66.1,
  80.93333333333334,
  92.33333333333333,
  112.23333333333333,
  132.46666666666667,
  148.96666666666667,
  185.33333333333334,
  196.96666666666667,
  224.5,
  262.7,
  272.1,
  282.4,
  305.6666666666667,
  351.73333333333335,
  396.7,
  512.6333333333333,
  670.2,
  780.6666666666666),
 (0, 1, 2, 1, 0, -1, 0, -1, -2, -1, 0, 1, 2, 1, 0, 1, 2, 1, 0, -1, -2)]

In [70]:
results_df = pd.DataFrame(res)
results_df
results_df.to_csv('maxvstpe/momentum_results.csv', index=False, header=False)

## Kaz vs sito

In [60]:
import pandas as pd

boxes_df = pd.read_csv('kazvssito/boxes.csv', header=None)
boxes_df.head()

0    1     2    3
0  963  353  1033  416
1  962  354  1033  417
2  962  353  1033  416
3  962  353  1033  416
4  963  353  1033  416

In [64]:
cap = cv2.VideoCapture("kazvssito/masked.mp4")
framecount = 0
reader = easyocr.Reader(['en'])
momentum = [[1, 0]] # Frame number, score
netScore = 0 # Left positive, Right negative

# Variables to keep track of number of frames number has changed
leftCount = 0
rightCount = 0

# These two variables are to check if the number should be the same
leftSameCount = 0
rightSameCount = 0

# Variables to keep track of current score
currL = 0
currR = 0

# Variables to ensure that we can capture the scoreboard
cantFindCount = 0
found = False
posList = []
def onMousePisteCorners(event, x, y, flags, param):
   global posList
   if event == cv2.EVENT_LBUTTONDOWN:
        posList.append([x, y])

pts2 = [[0,0], [0,360], [540,0], [540,360]]

while(True):
    ret, frame = cap.read()
    
    if ret == True:

        if not found:
            boxlist = boxes_df.iloc[framecount]
        frame = frame[int(boxlist[1])-20:int(boxlist[3])+20, int(boxlist[0])-20:int(boxlist[2])+20]
        
        res = cv2.resize(frame,None,fx=8, fy=8, interpolation = cv2.INTER_CUBIC)
        if not found:
            cv2.imshow('WindowName', res)
            cv2.setMouseCallback('WindowName', onMousePisteCorners)

            while(1):
                if cv2.waitKey(10) & 0xFF==ord('q'):
                    cv2.destroyAllWindows()
                    break
            posList = np.float32(posList)
            pts2 = np.float32(pts2)
            found = True

        gray = cv2.cvtColor(res, cv2.COLOR_BGR2GRAY)
        
        ret, newimage = cv2.threshold(gray,100,255,cv2.THRESH_BINARY_INV)
        frame = newimage
        
        matrix = cv2.getPerspectiveTransform(posList, pts2)
        frame = cv2.warpPerspective(frame, matrix, (540,360))
        h = frame.shape[0]
        w = frame.shape[1]
        
        resL = reader.recognize(frame, [[0, int(w*0.37), int(h*0.57), h]], [], allowlist='0123456789')[0]
        resR = reader.recognize(frame, [[int(w*0.65), w, int(h*0.57), h]], [], allowlist='0123456789')[0]

        frame = cv2.rectangle(frame, (0, int(h*0.57)), (int(w*0.37), h), (0,0,0), 3)
        frame = cv2.rectangle(frame, (int(w*0.65), int(h*0.57)), (w, h), (0,0,0), 3)
        
        currL, currR, leftCount, rightCount, leftSameCount, rightSameCount, momentum = checkNumbers(resL, resR, currL, currR, leftCount, rightCount, leftSameCount, rightSameCount, framecount, momentum)
        
        if (resL[2] > 0.2 and resR[2] > 0.2):
            output = (resL[1], resR[1])
            print(output)
            
        if (resL[2] < 0.1 or resR[2] < 0.1):
            cantFindCount += 1
            if cantFindCount == 30:
                found = False
                posList = []
        else:
            cantFindCount = 0
                
        
        cv2.imshow('frame',frame)
        framecount += 1
        if cv2.waitKey(1) & 0xFF == ord('r'):
            found = False
            posList = []
        if cv2.waitKey(1) & 0xFF == ord('q'):
            break
    else:
        break
cv2.destroyAllWindows() 
cap.release()

('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('9', '0')
('9', '0')
('7', '0')
('7', '0')
('7', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '9')
('0', '1')
('0', '1')
('0', '5')
('0', '2')
('0', '0')
('0', '0')
('0', '0')
('8', '0')
('8', '0')
('8', '0')
('8', '0')
('8', '0')
('8', '0')
('0', '0')
('0', '0')
('1', '0')
('3', '0')
('1', '1')
('1', '1')
('3', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '6')
('0', '0')
('0', '0')
('0', '3')
('8', '0')
('0', '0')
('8', '0')
('8', '0')
('0', '0')
('40', '7')
('0', '0')
('0', '0')
('0', '0'

('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')

('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('3', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '2')
('0', '20')
('0', '2')
('0', '29')
('0', '3')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0

('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')

('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '8')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')

...

('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('1', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('1', '5')
('1', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('11', '5')
('1', '5')
('1', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2',

('82', '5')
('82', '5')
('82', '5')
('82', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('82', '5')
('82', '5')
('2', '5')
('82', '5')
('82', '5')
('82', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('82', '5')
('82', '5')
('82', '5')
('82', '5')
('82', '5')
('82', '5')
('82', '5')
('82', '5')
('82', '5')
('82', '5')
('82', '5')
('82', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')


('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')

('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('43', '5')
('43', '5')
('43', '5')
('43', '5')
('43', '5')
('43', '5')
('43', '5')
('3', '5')
('43', '5')
('43', '5')
('43', '5')
('43', '5')
('3', '5')
('43', '5')
('43', '5')
('43', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('43', '5')
('43', '5')
('43', '5')
('43', '5')
('43', '5')
('43', '5')
('43', '5')
('43', '5')
('43', '5')
('43', '5')
('43', '5')
('43', '5')
('43', '5')
('43', '5')
('43', '5')
('43', '5')
('43', '5')
('43', '5')
('3', '5')
('3', '5')
('4', '5')
('3', '5')
('3', '5')
('3', '5')
('43', '5')
('43', '5')
('43', '5')
('43', '5')
('43', '5')
('3', '5')
('3', '5')
('3', '5')
('43', '5')
('43', '5')
('43', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '45')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('43', '5')
('43', '5')
('43', '5')
('43', '5')
('43', '5')
('43', '5')
('43', 

('14', '5')
('14', '5')
('14', '5')
('14', '5')
('84', '5')
('14', '5')
('84', '5')
('84', '5')
('84', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('84', '5')
('84', '5')
('14', '5')
('84', '5')
('84', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('84', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('14', '5')
('84', '5')
('84', '5')
('84', '5')
('14', '5')
('14

In [65]:
res = []
print(len(momentum))
for m in momentum:
    res.append([m[0] / 30, m[1]])
result = list(zip(*res))
result

22


[(0.03333333333333333,
  3.3,
  108.8,
  173.16666666666666,
  173.66666666666666,
  190.93333333333334,
  220.66666666666666,
  338.6,
  391.76666666666665,
  437.6333333333333,
  478.3333333333333,
  511.1333333333333,
  540.4666666666667,
  668.3,
  668.9666666666667,
  744.7333333333333,
  774.3333333333334,
  796.1333333333333,
  859.6,
  884.3333333333334,
  897.0,
  904.9333333333333),
 (0, 1, 0, -1, 0, 1, 2, 1, 2, 3, 4, 5, 4, 3, 4, 5, 6, 7, 8, 9, 8, 9)]

In [66]:
results_df = pd.DataFrame(res)
results_df
results_df.to_csv('kazvssito/momentum_results.csv', index=False, header=False)

## Indvssam

In [3]:
import pandas as pd

boxes_df = pd.read_csv('indvssam/boxes.csv', header=None)
boxes_df.head()

0    1    2    3
0  874  334  951  407
1  873  334  950  407
2  873  334  950  407
3  873  334  950  407
4  873  333  950  407

### Checking bounding box

In [19]:
cap = cv2.VideoCapture("indvssam/masked.mp4")
frame_width = int(cap.get(3))
frame_height = int(cap.get(4))
fourcc = cv2.VideoWriter_fourcc(*'mp4v')
out = cv2.VideoWriter('boundingbox.mp4',fourcc, 30, (frame_width,frame_height))
framecount = 0

while(True):
    ret, frame = cap.read()
    
    if ret == True:

                    
        boxlist = boxes_df.iloc[framecount]

        frame = cv2.rectangle(frame, (boxlist[0], boxlist[1]), (boxlist[2], boxlist[3]), (0,255,0), 1)
        
        cv2.imshow('frame',frame)
        out.write(frame)
        framecount += 1
        if cv2.waitKey(1) & 0xFF == ord('q'):
            break
    else:
        break
cv2.destroyAllWindows() 
cap.release()
out.release()

In [5]:
cap = cv2.VideoCapture("indvssam/masked.mp4")
framecount = 0
reader = easyocr.Reader(['en'])
momentum = [[1, 0]] # Frame number, score
netScore = 0 # Left positive, Right negative

# Variables to keep track of number of frames number has changed
leftCount = 0
rightCount = 0

# These two variables are to check if the number should be the same
leftSameCount = 0
rightSameCount = 0

# Variables to keep track of current score
currL = 0
currR = 0

# Variables to ensure that we can capture the scoreboard
cantFindCount = 0
found = False
posList = []
def onMousePisteCorners(event, x, y, flags, param):
   global posList
   if event == cv2.EVENT_LBUTTONDOWN:
        posList.append([x, y])

pts2 = [[0,0], [0,360], [540,0], [540,360]]

while(True):
    ret, frame = cap.read()
    
    if ret == True:

        if not found:
            boxlist = boxes_df.iloc[framecount]
        frame = frame[int(boxlist[1])-20:int(boxlist[3])+20, int(boxlist[0])-20:int(boxlist[2])+20]
        
        res = cv2.resize(frame,None,fx=8, fy=8, interpolation = cv2.INTER_CUBIC)
        if not found:
            cv2.imshow('WindowName', res)
            cv2.setMouseCallback('WindowName', onMousePisteCorners)

            while(1):
                if cv2.waitKey(10) & 0xFF==ord('q'):
                    cv2.destroyAllWindows()
                    break
            posList = np.float32(posList)
            pts2 = np.float32(pts2)
            found = True

        gray = cv2.cvtColor(res, cv2.COLOR_BGR2GRAY)
        
        ret, newimage = cv2.threshold(gray,100,255,cv2.THRESH_BINARY_INV)
        frame = newimage
        
        matrix = cv2.getPerspectiveTransform(posList, pts2)
        frame = cv2.warpPerspective(frame, matrix, (540,360))
        h = frame.shape[0]
        w = frame.shape[1]
        
        resL = reader.recognize(frame, [[0, int(w*0.37), int(h*0.57), h]], [], allowlist='0123456789')[0]
        resR = reader.recognize(frame, [[int(w*0.65), w, int(h*0.57), h]], [], allowlist='0123456789')[0]

        frame = cv2.rectangle(frame, (0, int(h*0.57)), (int(w*0.37), h), (0,0,0), 3)
        frame = cv2.rectangle(frame, (int(w*0.65), int(h*0.57)), (w, h), (0,0,0), 3)
        
        currL, currR, leftCount, rightCount, leftSameCount, rightSameCount, momentum = checkNumbers(resL, resR, currL, currR, leftCount, rightCount, leftSameCount, rightSameCount, framecount, momentum)
        
        if (resL[2] > 0.2 and resR[2] > 0.2):
            output = (resL[1], resR[1])
            print(output)
            
        if (resL[2] < 0.1 or resR[2] < 0.1):
            cantFindCount += 1
            if cantFindCount == 30:
                found = False
                posList = []
        else:
            cantFindCount = 0
                
        
        cv2.imshow('frame',frame)
        framecount += 1
        if cv2.waitKey(1) & 0xFF == ord('r'):
            found = False
            posList = []
        if cv2.waitKey(1) & 0xFF == ord('q'):
            break
    else:
        break
cv2.destroyAllWindows() 
cap.release()

('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('8', '0')
('8', '0')
('8', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('8', '8')
('8', '0')
('0', '0')
('0', '8')
('0', '0')
('8', '0')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '0')
('0', '0')
('0', '8')
('0', '8')
('0', '8')
('8', '8')
('0', '0')
('0', '8')
('0', '8')
('8', '8')
('0', '8')
('0', '8')
('8', '8')
('8', '8')
('0', '8')
('0', '8')
('0', '8')
('8', '8')
('0', '8')
('8', '8')
('8', '0')
('8', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '8')
('0', '8')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '8')
('8', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '8')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('8', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')

('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')
('0', '1')

('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')
('0', '2')

('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')

('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')
('0', '3')

...

('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7'

('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '2')
('7', '2')
('7', '2')
('7', '2')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '82')
('7', '8

('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7'

('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '13')
('7', '14')
('7', '04')
('7', '04')
('7', '04')
('7', '04')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7'

('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('7', '15')
('1', '15')
('1', '15')
('1', '85')
('1', '85')
('7', '15')
('7', '15')
('1', '15')
('1', '85')
('1', '85')
('1', '85')
('7', '85')
('7', '85')
('7', '85')
('7', '85')
('7', '85')
('7', '85')
('7', '85')
('7', '85')
('7', '85')
('77', '85')
('77', '85')
('7', '85')
('77', '85')
('77', '85')
('7', '15')
('7', '15')
('7', '85')
('77', '85')
('77', '85')
('77', '85')
('77', '85')
('7', '8

In [6]:
res = []
print(len(momentum))
for m in momentum:
    res.append([m[0] / 30, m[1]])
result = list(zip(*res))
result

23


[(0.03333333333333333,
  22.666666666666668,
  40.3,
  81.83333333333333,
  165.5,
  207.16666666666666,
  242.93333333333334,
  458.6666666666667,
  474.1,
  487.3,
  508.53333333333336,
  526.7666666666667,
  550.1333333333333,
  572.8333333333334,
  608.2333333333333,
  637.7333333333333,
  699.2,
  831.9,
  849.4,
  1136.6666666666667,
  1171.8,
  1209.9,
  1231.7666666666667),
 (0,
  -1,
  -2,
  -3,
  -4,
  -3,
  -4,
  -5,
  -4,
  -5,
  -6,
  -5,
  -6,
  -7,
  -6,
  -5,
  -6,
  -5,
  -4,
  -5,
  -6,
  -7,
  -8)]

In [59]:
results_df = pd.DataFrame(res)
results_df
results_df.to_csv('indvssam/momentum_results.csv', index=False, header=False)

## Danvskaz

In [37]:
import pandas as pd

boxes_df = pd.read_csv('danvskaz/boxes.csv', header=None)
boxes_df.head()

0    1    2    3
0  924  354  991  406
1  925  354  991  406
2  924  355  991  406
3  923  355  990  406
4  924  354  991  406

In [41]:
cap = cv2.VideoCapture("danvskaz/masked.mp4")
framecount = 0
reader = easyocr.Reader(['en'])
momentum = [[1, 0]] # Frame number, score
netScore = 0 # Left positive, Right negative

# Variables to keep track of number of frames number has changed
leftCount = 0
rightCount = 0

# These two variables are to check if the number should be the same
leftSameCount = 0
rightSameCount = 0

# Variables to keep track of current score
currL = 0
currR = 0

# Variables to ensure that we can capture the scoreboard
cantFindCount = 0
found = False
posList = []
def onMousePisteCorners(event, x, y, flags, param):
   global posList
   if event == cv2.EVENT_LBUTTONDOWN:
        posList.append([x, y])

pts2 = [[0,0], [0,360], [540,0], [540,360]]

while(True):
    ret, frame = cap.read()
    
    if ret == True:

        if not found:
            boxlist = boxes_df.iloc[framecount]
        frame = frame[int(boxlist[1])-20:int(boxlist[3])+20, int(boxlist[0])-20:int(boxlist[2])+20]
        
        res = cv2.resize(frame,None,fx=8, fy=8, interpolation = cv2.INTER_CUBIC)
        if not found:
            cv2.imshow('WindowName', res)
            cv2.setMouseCallback('WindowName', onMousePisteCorners)

            while(1):
                if cv2.waitKey(10) & 0xFF==ord('q'):
                    cv2.destroyAllWindows()
                    break
            posList = np.float32(posList)
            pts2 = np.float32(pts2)
            found = True

        gray = cv2.cvtColor(res, cv2.COLOR_BGR2GRAY)
        
        ret, newimage = cv2.threshold(gray,100,255,cv2.THRESH_BINARY_INV)
        frame = newimage
        
        matrix = cv2.getPerspectiveTransform(posList, pts2)
        frame = cv2.warpPerspective(frame, matrix, (540,360))
        h = frame.shape[0]
        w = frame.shape[1]
        
        resL = reader.recognize(frame, [[0, int(w*0.37), int(h*0.57), h]], [], allowlist='0123456789')[0]
        resR = reader.recognize(frame, [[int(w*0.65), w, int(h*0.57), h]], [], allowlist='0123456789')[0]

        frame = cv2.rectangle(frame, (0, int(h*0.57)), (int(w*0.37), h), (0,0,0), 3)
        frame = cv2.rectangle(frame, (int(w*0.65), int(h*0.57)), (w, h), (0,0,0), 3)
        
        currL, currR, leftCount, rightCount, leftSameCount, rightSameCount, momentum = checkNumbers(resL, resR, currL, currR, leftCount, rightCount, leftSameCount, rightSameCount, framecount, momentum)
        
        if (resL[2] > 0.2 and resR[2] > 0.2):
            output = (resL[1], resR[1])
            print(output)
            
        if (resL[2] < 0.1 or resR[2] < 0.1):
            cantFindCount += 1
            if cantFindCount == 30:
                found = False
                posList = []
        else:
            cantFindCount = 0
                
        
        cv2.imshow('frame',frame)
        framecount += 1
        if cv2.waitKey(1) & 0xFF == ord('r'):
            found = False
            posList = []
        if cv2.waitKey(1) & 0xFF == ord('q'):
            break
    else:
        break
cv2.destroyAllWindows() 
cap.release()

('0', '0')
('8', '0')
('0', '0')
('0', '0')
('8', '0')
('0', '0')
('0', '8')
('0', '8')
('0', '8')
('0', '0')
('0', '0')
('0', '8')
('0', '0')
('0', '8')
('0', '0')
('0', '0')
('0', '0')
('0', '9')
('0', '0')
('0', '8')
('0', '0')
('0', '0')
('0', '0')
('0', '8')
('0', '9')
('0', '8')
('0', '0')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')

('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')
('2', '1')

('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')

('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')

('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')
('3', '2')

...

('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11', '6')
('11

('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('42', '6')
('42', '6')
('42', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('12', '6')
('82', '6')
('82', '6')
('82', '6')
('82', '6')
('82', '6')
('82', '6')
('82', '6')
('82', '6')
('82', '6')
('82', '6')
('82', '6')
('82

('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')
('413', '6')

('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14', '6')
('14

('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')
('14', '37')

In [42]:
res = []
print(len(momentum))
for m in momentum:
    res.append([m[0] / 30, m[1]])
result = list(zip(*res))
result

22


[(0.03333333333333333,
  10.7,
  21.733333333333334,
  32.1,
  42.9,
  55.666666666666664,
  132.23333333333332,
  159.5,
  175.8,
  201.9,
  213.33333333333334,
  229.83333333333334,
  246.83333333333334,
  299.5,
  385.9,
  399.3333333333333,
  415.53333333333336,
  429.56666666666666,
  444.06666666666666,
  465.4,
  496.9,
  509.9),
 (0, 1, 0, 1, 2, 1, 0, -1, 0, 1, 2, 1, 2, 3, 4, 3, 4, 5, 6, 7, 8, 7)]

In [43]:
results_df = pd.DataFrame(res)
results_df
results_df.to_csv('danvskaz/momentum_results.csv', index=False, header=False)

## Luc vs james

In [44]:
import pandas as pd

boxes_df = pd.read_csv('luciusvsjames/boxes.csv', header=None)
boxes_df.head()

0    1     2    3
0  1114  220  1189  295
1  1116  219  1191  294
2  1117  219  1192  293
3  1113  218  1193  293
4  1117  218  1193  293

In [45]:
cap = cv2.VideoCapture("luciusvsjames/masked.mp4")
framecount = 0
reader = easyocr.Reader(['en'])
momentum = [[1, 0]] # Frame number, score
netScore = 0 # Left positive, Right negative

# Variables to keep track of number of frames number has changed
leftCount = 0
rightCount = 0

# These two variables are to check if the number should be the same
leftSameCount = 0
rightSameCount = 0

# Variables to keep track of current score
currL = 0
currR = 0

# Variables to ensure that we can capture the scoreboard
cantFindCount = 0
found = False
posList = []
def onMousePisteCorners(event, x, y, flags, param):
   global posList
   if event == cv2.EVENT_LBUTTONDOWN:
        posList.append([x, y])

pts2 = [[0,0], [0,360], [540,0], [540,360]]

while(True):
    ret, frame = cap.read()
    
    if ret == True:

        if not found:
            boxlist = boxes_df.iloc[framecount]
        frame = frame[int(boxlist[1])-20:int(boxlist[3])+20, int(boxlist[0])-20:int(boxlist[2])+20]
        
        res = cv2.resize(frame,None,fx=8, fy=8, interpolation = cv2.INTER_CUBIC)
        if not found:
            cv2.imshow('WindowName', res)
            cv2.setMouseCallback('WindowName', onMousePisteCorners)

            while(1):
                if cv2.waitKey(10) & 0xFF==ord('q'):
                    cv2.destroyAllWindows()
                    break
            posList = np.float32(posList)
            pts2 = np.float32(pts2)
            found = True

        gray = cv2.cvtColor(res, cv2.COLOR_BGR2GRAY)
        
        ret, newimage = cv2.threshold(gray,100,255,cv2.THRESH_BINARY_INV)
        frame = newimage
        
        matrix = cv2.getPerspectiveTransform(posList, pts2)
        frame = cv2.warpPerspective(frame, matrix, (540,360))
        h = frame.shape[0]
        w = frame.shape[1]
        
        resL = reader.recognize(frame, [[0, int(w*0.37), int(h*0.57), h]], [], allowlist='0123456789')[0]
        resR = reader.recognize(frame, [[int(w*0.65), w, int(h*0.57), h]], [], allowlist='0123456789')[0]

        frame = cv2.rectangle(frame, (0, int(h*0.57)), (int(w*0.37), h), (0,0,0), 3)
        frame = cv2.rectangle(frame, (int(w*0.65), int(h*0.57)), (w, h), (0,0,0), 3)
        
        currL, currR, leftCount, rightCount, leftSameCount, rightSameCount, momentum = checkNumbers(resL, resR, currL, currR, leftCount, rightCount, leftSameCount, rightSameCount, framecount, momentum)
        
        if (resL[2] > 0.2 and resR[2] > 0.2):
            output = (resL[1], resR[1])
            print(output)
            
        if (resL[2] < 0.1 or resR[2] < 0.1):
            cantFindCount += 1
            if cantFindCount == 30:
                found = False
                posList = []
        else:
            cantFindCount = 0
                
        
        cv2.imshow('frame',frame)
        framecount += 1
        if cv2.waitKey(1) & 0xFF == ord('r'):
            found = False
            posList = []
        if cv2.waitKey(1) & 0xFF == ord('q'):
            break
    else:
        break
cv2.destroyAllWindows() 
cap.release()

('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('4', '8')
('8', '8')
('8', '8')
('8', '8')
('0', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('1', '8')
('8', '8')
('0', '8')
('8', '8')
('8', '8')
('1', '8')
('0', '8')
('8', '8')
('8', '1')
('8', '3')
('0', '8')
('0', '8')
('8', '8')
('0', '8')
('1', '8')
('0', '8')
('0', '8')
('8', '3')
('1', '1')
('1', '8')
('0', '8')
('0', '8')
('1', '8')
('1', '8')
('1', '0')
('8', '0')
('0', '0')
('0', '40')
('0', '0')
('4', '40')
('4', '40')
('4', '40')
('4', '40')
('4', '40')
('4', '40')
('4', '40')
('4', '40')
('4', '40')
('4', '40')
('4', '40')
('4', '40')
('5', '4')
('5', '40')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '

('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')
('8', '8')

('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')
('2', '2')

('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '4')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')
('2', '5')

('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')
('3', '5')

...

('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('9', '12')
('9', '12')
('9', '12')
('9', '12')
('9', '12')
('9', '12')
('9', '12')
('9', '12')
('9', '12')
('9', '12')
('9', '12')
('9', '12')
('9', '12')
('9', '12')
('9', '12')
('9', '12')
('9', '12')
('9', '12')
('9', '12')
('9', '12')
('9', '12')
('9', '12')
('9', '12')
('9', '12')
('9', '12')
('9', '12')
('9', '12')
('9'

('8', '12')
('8', '12')
('88', '12')
('88', '12')
('88', '12')
('8', '12')
('8', '12')
('88', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '12')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('88', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('88', '13')
('88', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13

('8', '13')
('8', '13')
('8', '13')
('8', '13')
('8', '13')
('88', '13')
('88', '13')
('88', '13')
('88', '13')
('8', '13')
('88', '13')
('88', '13')
('88', '13')
('88', '13')
('88', '13')
('88', '13')
('88', '13')
('88', '13')
('88', '13')
('88', '13')
('88', '13')
('88', '13')
('8', '13')
('8', '13')
('8', '13')
('88', '13')
('88', '13')
('88', '13')
('88', '13')
('88', '13')
('88', '13')
('88', '13')
('88', '13')
('88', '13')
('88', '13')
('88', '13')
('88', '13')
('5', '13')
('5', '13')
('5', '13')
('5', '13')
('5', '13')
('5', '13')
('5', '13')
('5', '13')
('9', '13')
('9', '13')
('5', '13')
('5', '13')
('5', '13')
('9', '13')
('9', '13')
('9', '13')
('9', '13')
('9', '13')
('5', '13')
('5', '13')
('5', '13')
('5', '13')
('5', '13')
('5', '13')
('5', '13')
('5', '13')
('5', '13')
('5', '13')
('5', '13')
('5', '13')
('5', '13')
('5', '13')
('9', '13')
('9', '13')
('9', '13')
('9', '13')
('9', '13')
('9', '13')
('9', '13')
('9', '13')
('9', '13')
('5', '13')
('5', '13')
('5', '13')


('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('82', '14')
('13', '14')
('13', '14')
('13', '14')
('13', '14')
('13', '14')
('13', '14')
('13', '14')
('13', '14')
('13', '14')
('13', '14')
('83', '14')
('83', '14')
('13', '14')
('83', '14')
('13', '14')
('13', '14')
('13', '14')
('13', '14')
('13', '14')
('13', '14')
('13', '14')
('413', '14')
('13', '14')
('13', '14')
('13', '14')
('13', '14')
('13', '14')
('13', '14')
('13', '14')
('13', '14')
('13', '14')
('13', '14')
('13', '14')
('83', '14')
('83', '14')
('83', '14')
('83', '14')
('83', '14')
('13', '14')
('13', '14'

('413', '15')
('413', '15')
('413', '15')
('43', '15')
('43', '15')
('483', '15')
('483', '15')
('83', '15')
('413', '15')
('13', '15')
('13', '15')
('13', '15')
('413', '15')
('43', '15')
('413', '15')
('13', '15')
('413', '15')
('13', '15')
('413', '15')
('413', '15')
('413', '15')
('413', '15')
('413', '15')
('13', '15')
('83', '15')
('83', '15')
('83', '15')
('83', '15')
('83', '15')
('83', '15')
('83', '15')
('83', '15')
('413', '15')
('13', '15')
('413', '15')
('83', '15')
('43', '15')
('43', '15')
('43', '15')
('13', '15')
('13', '15')
('13', '15')
('43', '15')
('13', '15')
('83', '15')
('13', '15')
('43', '15')
('13', '15')
('13', '15')
('43', '15')
('83', '15')
('83', '15')
('83', '45')
('83', '45')
('43', '85')
('43', '85')
('13', '45')
('83', '85')
('3', '15')
('13', '15')
('83', '15')
('3', '15')


In [46]:
res = []
print(len(momentum))
for m in momentum:
    res.append([m[0] / 30, m[1]])
result = list(zip(*res))
result

11


[(0.03333333333333333,
  50.766666666666666,
  68.73333333333333,
  110.6,
  235.86666666666667,
  274.2,
  291.1666666666667,
  321.8666666666667,
  341.5,
  360.4,
  377.6666666666667),
 (0, 1, 2, 3, 4, 5, 6, 5, 6, 7, 8)]

In [14]:
results_df = pd.DataFrame(res)
results_df
results_df.to_csv('luciusvsjames/momentum_results.csv', index=False, header=False)

## Cheryl vs Japan

In [47]:
import pandas as pd

boxes_df = pd.read_csv('cherylvsjpn/boxes.csv', header=None)
boxes_df.head()

0    1    2    3
0  911  373  980  425
1  911  372  979  425
2  910  373  980  425
3  910  373  980  425
4  910  372  979  425

In [48]:
cap = cv2.VideoCapture("cherylvsjpn/masked.mp4")
framecount = 0
reader = easyocr.Reader(['en'])
momentum = [[1, 0]] # Frame number, score
netScore = 0 # Left positive, Right negative

# Variables to keep track of number of frames number has changed
leftCount = 0
rightCount = 0

# These two variables are to check if the number should be the same
leftSameCount = 0
rightSameCount = 0

# Variables to keep track of current score
currL = 0
currR = 0

# Variables to ensure that we can capture the scoreboard
cantFindCount = 0
found = False
posList = []
def onMousePisteCorners(event, x, y, flags, param):
   global posList
   if event == cv2.EVENT_LBUTTONDOWN:
        posList.append([x, y])

pts2 = [[0,0], [0,360], [540,0], [540,360]]

while(True):
    ret, frame = cap.read()
    
    if ret == True:

        if not found:
            boxlist = boxes_df.iloc[framecount]
        frame = frame[int(boxlist[1])-20:int(boxlist[3])+20, int(boxlist[0])-20:int(boxlist[2])+20]
        
        res = cv2.resize(frame,None,fx=8, fy=8, interpolation = cv2.INTER_CUBIC)
        if not found:
            cv2.imshow('WindowName', res)
            cv2.setMouseCallback('WindowName', onMousePisteCorners)

            while(1):
                if cv2.waitKey(10) & 0xFF==ord('q'):
                    cv2.destroyAllWindows()
                    break
            posList = np.float32(posList)
            pts2 = np.float32(pts2)
            found = True

        gray = cv2.cvtColor(res, cv2.COLOR_BGR2GRAY)
        
        ret, newimage = cv2.threshold(gray,100,255,cv2.THRESH_BINARY_INV)
        frame = newimage
        
        matrix = cv2.getPerspectiveTransform(posList, pts2)
        frame = cv2.warpPerspective(frame, matrix, (540,360))
        h = frame.shape[0]
        w = frame.shape[1]
        
        resL = reader.recognize(frame, [[0, int(w*0.37), int(h*0.57), h]], [], allowlist='0123456789')[0]
        resR = reader.recognize(frame, [[int(w*0.65), w, int(h*0.57), h]], [], allowlist='0123456789')[0]

        frame = cv2.rectangle(frame, (0, int(h*0.57)), (int(w*0.37), h), (0,0,0), 3)
        frame = cv2.rectangle(frame, (int(w*0.65), int(h*0.57)), (w, h), (0,0,0), 3)
        
        currL, currR, leftCount, rightCount, leftSameCount, rightSameCount, momentum = checkNumbers(resL, resR, currL, currR, leftCount, rightCount, leftSameCount, rightSameCount, framecount, momentum)
        
        if (resL[2] > 0.2 and resR[2] > 0.2):
            output = (resL[1], resR[1])
            print(output)
            
        if (resL[2] < 0.1 or resR[2] < 0.1):
            cantFindCount += 1
            if cantFindCount == 30:
                found = False
                posList = []
        else:
            cantFindCount = 0
                
        
        cv2.imshow('frame',frame)
        framecount += 1
        if cv2.waitKey(1) & 0xFF == ord('r'):
            found = False
            posList = []
        if cv2.waitKey(1) & 0xFF == ord('q'):
            break
    else:
        break
cv2.destroyAllWindows() 
cap.release()

('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')

('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')
('0', '8')

('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')

('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')
('1', '8')

('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')

...

('5', '01')
('5', '01')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '01')
('5', '01')
('5', '01')
('5', '01')
('5', '01')
('5', '01')
('5', '01')
('5', '01')
('5', '01')
('5', '01')
('5', '01')
('5', '01')
('5', '01')
('5', '01')
('5', '01')
('5', '01')
('5', '01')
('5', '01')
('5', '01')
('5', '01')
('5', '01')
('5', '01')
('5', '01')
('5', '01')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '0')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5', '11')
('5'

('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5', '12')
('5'

('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5', '14')
('5'

('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7'

('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7'

In [49]:
res = []
print(len(momentum))
for m in momentum:
    res.append([m[0] / 30, m[1]])
result = list(zip(*res))
result

23


[(0.03333333333333333,
  32.43333333333333,
  97.46666666666667,
  114.06666666666666,
  114.56666666666666,
  212.7,
  327.3333333333333,
  380.8333333333333,
  381.3,
  411.8,
  491.0,
  513.2,
  513.6333333333333,
  535.0333333333333,
  665.3666666666667,
  665.8666666666667,
  682.6666666666666,
  702.7,
  724.8666666666667,
  740.8666666666667,
  751.8666666666667,
  763.9666666666667,
  794.3),
 (0,
  1,
  0,
  1,
  0,
  -1,
  -2,
  -1,
  -2,
  -3,
  -4,
  -3,
  -4,
  -5,
  -4,
  -5,
  -6,
  -7,
  -8,
  -9,
  -8,
  -7,
  -8)]

In [50]:
results_df = pd.DataFrame(res)
results_df
results_df.to_csv('cherylvsjpn/momentum_results.csv', index=False, header=False)

## Elle vs kor

In [20]:
import pandas as pd

boxes_df = pd.read_csv('ellevskor/boxes.csv', header=None)
boxes_df.head()

0    1    2    3
0  724  235  804  310
1  724  235  803  310
2  724  235  803  310
3  724  235  803  310
4  724  235  803  310

In [21]:
cap = cv2.VideoCapture("ellevskor/masked.mp4")
framecount = 0
reader = easyocr.Reader(['en'])
momentum = [[1, 0]] # Frame number, score
netScore = 0 # Left positive, Right negative

# Variables to keep track of number of frames number has changed
leftCount = 0
rightCount = 0

# These two variables are to check if the number should be the same
leftSameCount = 0
rightSameCount = 0

# Variables to keep track of current score
currL = 0
currR = 0

# Variables to ensure that we can capture the scoreboard
cantFindCount = 0
found = False
posList = []
def onMousePisteCorners(event, x, y, flags, param):
   global posList
   if event == cv2.EVENT_LBUTTONDOWN:
        posList.append([x, y])

pts2 = [[0,0], [0,360], [540,0], [540,360]]

while(True):
    ret, frame = cap.read()
    
    if ret == True:

        if not found:
            boxlist = boxes_df.iloc[framecount]
        frame = frame[int(boxlist[1])-20:int(boxlist[3])+20, int(boxlist[0])-20:int(boxlist[2])+20]
        
        res = cv2.resize(frame,None,fx=8, fy=8, interpolation = cv2.INTER_CUBIC)
        if not found:
            cv2.imshow('WindowName', res)
            cv2.setMouseCallback('WindowName', onMousePisteCorners)

            while(1):
                if cv2.waitKey(10) & 0xFF==ord('q'):
                    cv2.destroyAllWindows()
                    break
            posList = np.float32(posList)
            pts2 = np.float32(pts2)
            found = True

        gray = cv2.cvtColor(res, cv2.COLOR_BGR2GRAY)
        
        ret, newimage = cv2.threshold(gray,100,255,cv2.THRESH_BINARY_INV)
        frame = newimage
        
        matrix = cv2.getPerspectiveTransform(posList, pts2)
        frame = cv2.warpPerspective(frame, matrix, (540,360))
        h = frame.shape[0]
        w = frame.shape[1]
        
        resL = reader.recognize(frame, [[0, int(w*0.37), int(h*0.57), h]], [], allowlist='0123456789')[0]
        resR = reader.recognize(frame, [[int(w*0.65), w, int(h*0.57), h]], [], allowlist='0123456789')[0]

        frame = cv2.rectangle(frame, (0, int(h*0.57)), (int(w*0.37), h), (0,0,0), 3)
        frame = cv2.rectangle(frame, (int(w*0.65), int(h*0.57)), (w, h), (0,0,0), 3)
        
        currL, currR, leftCount, rightCount, leftSameCount, rightSameCount, momentum = checkNumbers(resL, resR, currL, currR, leftCount, rightCount, leftSameCount, rightSameCount, framecount, momentum)
        
        if (resL[2] > 0.2 and resR[2] > 0.2):
            output = (resL[1], resR[1])
            print(output)
            
        if (resL[2] < 0.1 or resR[2] < 0.1):
            cantFindCount += 1
            if cantFindCount == 30:
                found = False
                posList = []
        else:
            cantFindCount = 0
                
        
        cv2.imshow('frame',frame)
        framecount += 1
        if cv2.waitKey(1) & 0xFF == ord('r'):
            found = False
            posList = []
        if cv2.waitKey(1) & 0xFF == ord('q'):
            break
    else:
        break
cv2.destroyAllWindows() 
cap.release()

('0', '0')
('0', '8')
('0', '0')
('0', '0')
('8', '0')
('8', '0')
('0', '0')
('8', '0')
('8', '0')
('8', '0')
('8', '0')
('8', '0')
('8', '0')
('8', '0')
('8', '0')
('8', '0')
('8', '0')
('8', '0')
('8', '0')
('8', '8')
('0', '0')
('0', '0')
('8', '0')
('8', '0')
('8', '0')
('8', '0')
('8', '8')
('8', '8')
('0', '8')
('8', '0')
('8', '0')
('8', '0')
('8', '0')
('8', '8')
('8', '0')
('8', '0')
('8', '0')
('8', '0')
('8', '0')
('8', '0')
('0', '0')
('8', '0')
('8', '0')
('8', '0')
('8', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('8', '0')
('8', '0')
('0', '8')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('8', '0')
('0', '0')
('8', '0')
('8', '0')
('8', '0')
('8', '0')
('8', '0')
('8', '0')
('8', '0')
('8', '0')
('8', '8')
('0', '0')
('0', '8')
('0', '8')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')

('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')
('0', '0')

('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')

('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')
('1', '0')

('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')
('1', '1')

...

('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6', '11')
('6'

('6', '12')
('6', '12')
('6', '82')
('6', '82')
('6', '12')
('6', '12')
('6', '82')
('6', '82')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '12')
('6', '82')
('6', '12')
('6', '12')
('6', '82')
('6', '82')
('6', '12')
('6', '12')
('6', '12')
('6', '82')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6'

('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '12')
('6', '12')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '12')
('6', '12')
('6', '12')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '12')
('6', '12')
('6', '82')
('6', '12')
('6', '12')
('6', '12')
('6', '12')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6', '82')
('6'

('6', '13')
('6', '13')
('6', '13')
('6', '13')
('6', '13')
('6', '13')
('6', '13')
('6', '13')
('6', '13')
('6', '13')
('6', '13')
('6', '13')
('6', '13')
('6', '13')
('6', '13')
('6', '13')
('6', '13')
('6', '13')
('6', '13')
('6', '15')
('6', '14')
('6', '14')
('6', '14')
('6', '14')
('6', '14')
('6', '14')
('6', '14')
('6', '14')
('6', '14')
('6', '14')
('6', '14')
('6', '14')
('6', '14')
('6', '14')
('6', '14')
('6', '14')
('6', '14')
('6', '14')
('6', '14')
('6', '14')
('6', '14')
('6', '14')
('6', '14')
('6', '14')
('6', '14')
('6', '14')
('6', '14')
('6', '14')
('6', '14')
('6', '14')
('6', '14')
('6', '14')
('8', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7'

('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7', '14')
('7'

In [22]:
res = []
print(len(momentum))
for m in momentum:
    res.append([m[0] / 30, m[1]])
result = list(zip(*res))
result

23


[(0.03333333333333333,
  50.2,
  84.73333333333333,
  127.66666666666667,
  152.63333333333333,
  181.96666666666667,
  328.3666666666667,
  372.3,
  383.6666666666667,
  413.53333333333336,
  449.1333333333333,
  451.3666666666667,
  505.46666666666664,
  527.2666666666667,
  541.8666666666667,
  558.5666666666667,
  580.2,
  656.2,
  681.6666666666666,
  711.2,
  729.5666666666667,
  730.6666666666666,
  765.4666666666667),
 (0,
  1,
  0,
  -1,
  -2,
  -1,
  -2,
  -1,
  -2,
  -3,
  -2,
  -3,
  -4,
  -3,
  -4,
  -3,
  -4,
  -5,
  -6,
  -7,
  -8,
  -7,
  -8)]

In [23]:
results_df = pd.DataFrame(res)
results_df
results_df.to_csv('ellevskor/momentum_results.csv', index=False, header=False)